In [73]:
import numpy as np

TRNG_PAIR_CNT = 64


if __name__ == '__main__':
    # reading info file - length of trace, sampling frequency (not necessary to know in our case), random value generated by the TRNG
    with open("data_info.txt", "r") as fin:
        tracelen = int(fin.readline())
        fs = int(fin.readline())
        trng_val = fin.readline()

    traces = np.fromfile("data.bin", dtype='uint8') # reading traces for individual ROs
    traces = np.reshape(traces, (traces.size//tracelen, tracelen)) # reshape of matrix, each row contains the trace for one RO

    traces_bin = traces > 128 # conversion of waveforms to rectangles - everything below threshold is 0, otherwise 1 (they are boolean values actually)
    print(traces)
    print(traces_bin.shape)
    rising_edges = np.logical_not(traces_bin[:,:-1]) & traces_bin[:,1:] # finding rising edges, each rising edge is represented by True

    cnt = np.count_nonzero(rising_edges, axis=1) # count the number of rising edges in rows
    
    # cnt is now a 1D vector
    cnt = cnt.reshape(TRNG_PAIR_CNT,2).min(axis=1) # Reshape of the count array into matrix, where each row contains 2 values - the number of rising edges for two ROs in a pair. Then we select the smaller value.
    
    cnt_sel = cnt & 0b00000011 # select only the two least significant bits

    estimate = ''.join([np.binary_repr(x, width=2) for x in cnt_sel]) # binary representation of the values (the last 2 bits) and joining them into one string
    estimate = '{0:0>32x}'.format(int(estimate, 2))
    # from data_info, output of the RNG in FPGA
    print(trng_val[:-1] == estimate)

[[44 44 45 ... 43 44 44]
 [44 45 45 ... 45 45 45]
 [44 45 45 ... 44 44 44]
 ...
 [45 45 45 ... 46 45 46]
 [44 44 45 ... 45 45 45]
 [45 46 45 ... 45 45 46]]
(128, 750000)
[59867 59631 64874 55734 51531 64641 63078 56084 62793 54154 50676 62981
 55136 62640 58096 48365 62697 51194 54140 57243 59968 63117 45133 61542
 59420 59012 61305 63438 58405 57121 62630 56219 54454 50854 65426 51115
 47308 42314 54576 63390 62825 51672 51684 60670 51151 49354 51373 61212
 61200 49430 64257 58178 63377 62001 57011 64714 64740 54700 56772 63292
 57779 59093 61834 61733]
True

